In [1]:
 !pip install pm4py pandas

import pandas as pd
from pm4py.objects.log.util import dataframe_utils
from pm4py.objects.conversion.log import converter as log_converter
from pm4py.algo.discovery.dfg import algorithm as dfg_discovery

file_path = "/content/오타(대문자, 띄어쓰기, 알파벳 누락 등)-0.1-0.csv"
df = pd.read_csv(file_path)

df_pm4py = df.rename(columns={
    "Case": "case:concept:name",
    "Activity": "concept:name",
    "Timestamp": "time:timestamp"
})
df_pm4py["time:timestamp"] = pd.to_datetime(df_pm4py["time:timestamp"])
df_pm4py = dataframe_utils.convert_timestamp_columns_in_df(df_pm4py)


log = log_converter.apply(df_pm4py, variant=log_converter.Variants.TO_EVENT_LOG)
dfg = dfg_discovery.apply(log)
dfg_text = [f"{source} -> {target} : {count}" for (source, target), count in dfg.items()]


for line in dfg_text:
    print(line)

with open("DFG_as_text1.txt", "w") as f:
    for line in dfg_text:
        f.write(line + "\n")

print("DFG 전처리 완료 및 저장 완료!")


  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 43.5 MB/s eta 0:00:00
  Created wheel for intervaltree: filename=intervaltree-3.1.0-py2.py3-none-any.whl size=26098 sha256=3871f7b6edb95c2ff577ddebfb4e7b824c68710c23806be43ea39684545cc40e
  Stored in directory: /root/.cache/pip/wheels/31/d7/d9/eec6891f78cac19a693bd40ecb8365d2f4613318c145ec9816
Successfully built intervaltree


FileNotFoundError: [Errno 2] No such file or directory: '/content/오타(대문자, 띄어쓰기, 알파벳 누락 등)-0.1-0.csv'

In [2]:
!pip install pm4py pandas
import pandas as pd
from collections import defaultdict
from pm4py.objects.log.util import dataframe_utils
from pm4py.objects.conversion.log import converter as log_converter

# CSV 불러오기
file_path = "/content/오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-0.csv"
df = pd.read_csv(file_path)

# PM4Py 포맷으로 변환
df_pm4py = df.rename(columns={
    "Case": "case:concept:name",
    "Activity": "concept:name",
    "Timestamp": "time:timestamp"
})
df_pm4py["time:timestamp"] = pd.to_datetime(df_pm4py["time:timestamp"])
df_pm4py = dataframe_utils.convert_timestamp_columns_in_df(df_pm4py)

# Case별 Activity 시퀀스 추출
trace_dict = df_pm4py.groupby("case:concept:name")["concept:name"].apply(list).to_dict()

# Case ID를 포함한 DFG 생성
dfg_count_map = defaultdict(int)
dfg_text = []

for case_id, activity_list in trace_dict.items():
    for i in range(len(activity_list) - 1):
        source = f"{activity_list[i]}({case_id})"
        target = f"{activity_list[i + 1]}({case_id})"
        edge_str = f"{source} -> {target}"
        dfg_count_map[edge_str] += 1

# 출력용 텍스트 구성
for edge_str, count in dfg_count_map.items():
    dfg_text.append(f"{edge_str} : {count}")

# 결과 출력
for line in dfg_text:
    print(line)

# 파일 저장
with open("DFG_new.txt", "w", encoding="utf-8") as f:
    for line in dfg_text:
        f.write(line + "\n")

print("✅ DFG with Activity(case_id) 형식 저장 완료!")


/usr/local/lib/python3.11/dist-packages/cudf/core/groupby/groupby.py:1759: RuntimeWarning: GroupBy.apply() performance scales poorly with number of groups. Got 557 groups. Some functions may perform better by passing engine='jit'
  warnings.warn(


register submission date request_RNvnAvOp_560872(2760925) -> phase application received(2760925) : 1
register submission date request(2771451) -> enter senddate procedure confirmation(2771451) : 1
enter senddate procedure confirmation(2771451) -> subcases completeness completed(2771451) : 1
subcases completeness completed(2771451) -> enter senddate acknowledgement(2771451) : 1
enter senddate acknowledgement(2771451) -> enter senddate retrieve missing data(2771451) : 1
enter senddate retrieve missing data(2771451) -> enter receipt of additional data(2771451) : 1
enter receipt of additional data(2771451) -> enter senddate procedure confirmation(2771451) : 1
enter senddate procedure confirmation(2771451) -> registrer date of publishing received request(2771451) : 1
registrer date of publishing received request(2771451) -> enter senddate procedure confirmation(2771451) : 1
enter senddate procedure confirmation(2771451) -> subcases completeness completed_UEXExIZV_6(2771451) : 1
subcases com

In [ ]:
import openai

client = openai.OpenAI(api_key="")

with open("DFG_new.txt", "r") as f:
    lines = f.readlines()

chunk_size = 20
chunks = [lines[i:i+chunk_size] for i in range(0, len(lines), chunk_size)]

all_results = []

for i, chunk in enumerate(chunks):
    preprocessed_text = "".join(chunk)


    prompt = f"""
You are a business process analysis expert. The following data represents a process mining event log, where each activity reflects a specific action within a business process. These logs typically include sequences of activities tied to individual case IDs (process instances), and can be used to discover, monitor, and improve real-world processes.

Your task is to detect anomalies in activity labels that contain meaningless or artificially generated suffixes.

Please analyze the following process description and identify any activity names that appear to contain garbled, irrelevant, or randomly generated strings appended to the end of otherwise valid activity names.

Examples (for reference only — not exhaustive):
- "register submission date request_RNvnAvOp_560872"
- "transcript decision environmental permit to stakeholders_DmQUbIVJ_560462"
- "applicant is stakeholder_yTeCyyrk_560431"

Detection Criteria:
- The core activity name is a valid business process term.
- The suffix (after an underscore) is meaningless, random, or non-informative.
- The suffix may contain random characters, IDs, or alphanumeric noise.
- Do not include activities with typos, casing errors, or missing characters — only suffix pollution.

Each activity label is followed by a case ID in parentheses. For example:
register submission date request_RNvnAvOp_560872(3027880)

In this case, the case ID is 3027880. Use this ID when reporting.

Output format (clear and concise):
Case ID: <case_id>
Activity: <full polluted activity label>

Only report actual anomalies. If no anomaly is found in the chunk, return:
No anomaly found.

Process Description:
{preprocessed_text}

"""


    # GPT-3.5-turbo 호출
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a business process analysis expert."},
            {"role": "user", "content": prompt}
        ],
        temperature=0.2,
        max_tokens=3000
    )

    result = response.choices[0].message.content
    all_results.append(result)

    print(f"\n=== 결과 (Chunk {i+1}) ===\n{result}")


with open("anomaly_results.txt", "w") as f:
    for chunk_result in all_results:
        f.write(chunk_result + "\n\n")

print("\n✅ 모든 Chunk 결과 저장 완료: anomaly_results_DFG.txt")


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
Case ID: 4972781  
Activity: regular procedure without MER_dmChhMyt_560872(4972781)

=== 결과 (Chunk 709) ===
Case ID: 4978339  
Activity: OLO messaging active_kjOATgGp_560925(4978339)

Case ID: 4978339  
Activity: reception through OLO_CsyXVeeu_560925(4978339)

Case ID: 4978339  
Activity: enter senddate acknowledgement_nMjcfqnC_560925(4978339)

Case ID: 4978339  
Activity: forward to the competent authority_ZEYJxQUM_560925(4978339)

Case ID: 4978339  
Activity: regular procedure without MER_YcJWnclc_560925(4978339)

=== 결과 (Chunk 710) ===
Case ID: 4978339  
Activity: no permit needed or only notification needed_tKQMKMqM_560912

Case ID: 4978339  
Activity: send letter in progress_MGsRLTbx_560912

Case ID: 5019310  
Activity: OLO messaging active_ZtNqJEfo_560912

=== 결과 (Chunk 711) ===
No anomaly found.

=== 결과 (Chunk 712) ===
Case ID: 5019310  
Activity: creating environmental permit decision_jUmiFKta_3273854(5019310)

Case ID: 5019310  
Activity: ge

In [17]:
import pandas as pd
import re

# 정답지 로드
gt = pd.read_csv("/content/오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-01.정답지.csv")
gt["is_polluted"] = gt["Injection"] == "polluted Label(Activity)"
gt["Activity"] = gt["Activity"].astype(str)

# 정답 activity 중 오류 라벨된 것만 추출
ground_truth_activities = set(gt[gt["is_polluted"]]["Activity"])

# anomaly_results.txt에서 유효한 Activity 추출 (Case ID 조건 포함)
with open("anomaly_results.txt", "r", encoding="utf-8") as f:
    lines = f.readlines()

predicted_activities = set()
current_case_id = None

for line in lines:
    case_match = re.search(r"Case ID\s*[:\-]?\s*(\d+)", line)
    activity_match = re.search(r"Activity\s*[:\-]?\s*(.+)", line)

    if case_match:
        current_case_id = int(case_match.group(1))

    if activity_match and current_case_id is not None:

            activity = activity_match.group(1).strip()
            activity = re.sub(r"\s*\(\d+\)", "", activity)  # 괄호 제거
            predicted_activities.add(activity)

# 정확도 비교
tp = len(predicted_activities & ground_truth_activities)
fp = len(predicted_activities - ground_truth_activities)
fn = len(ground_truth_activities - predicted_activities)

precision = tp / (tp + fp) if (tp + fp) else 0.0
recall = tp / (tp + fn) if (tp + fn) else 0.0
f1 = 2 * precision * recall / (precision + recall) if (precision + recall) else 0.0

# 출력
print(f"True Positives: {tp}")
print(f"False Positives: {fp}")
print(f"False Negatives: {fn}")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1 Score:  {f1:.4f}")


True Positives: 2492
False Positives: 188
False Negatives: 192
Precision: 0.9299
Recall:    0.9285
F1 Score:  0.9292


In [6]:
import pandas as pd

file_path = "/content/오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-0.csv"
df = pd.read_csv(file_path)

# Case별로 Activity 리스트 구성
trace_dict = df.groupby("Case")["Activity"].apply(list)

variant_dict = {}

# 각 Case ID에 대해 Activity 시퀀스를 문자열로 변환
for case_id, trace in trace_dict.items():
    # 각 activity 뒤에 (Case ID) 추가
    trace_with_case = [f"{activity}({case_id})" for activity in trace]
    trace_str = " -> ".join(trace_with_case)
    variant_dict[trace_str] = variant_dict.get(trace_str, 0) + 1

# 결과 출력
for i, (variant, count) in enumerate(variant_dict.items(), 1):
    print(f"Variant {i}: {variant} (Count: {count})")

# 파일 저장
with open("Trace_text.txt", "w", encoding="utf-8") as f:
    for i, (variant, count) in enumerate(variant_dict.items(), 1):
        f.write(f"Variant {i}: {variant} (Count: {count})\n")

print("✅ Trace Variants 전처리 완료 및 저장 완료!")


/usr/local/lib/python3.11/dist-packages/cudf/core/groupby/groupby.py:1759: RuntimeWarning: GroupBy.apply() performance scales poorly with number of groups. Got 557 groups. Some functions may perform better by passing engine='jit'
  warnings.warn(


Variant 1: register submission date request_RNvnAvOp_560872(2760925) -> phase application received(2760925) (Count: 1)
Variant 2: register submission date request(2771451) -> enter senddate procedure confirmation(2771451) -> subcases completeness completed(2771451) -> enter senddate acknowledgement(2771451) -> enter senddate retrieve missing data(2771451) -> enter receipt of additional data(2771451) -> enter senddate procedure confirmation(2771451) -> registrer date of publishing received request(2771451) -> enter senddate procedure confirmation(2771451) -> subcases completeness completed_UEXExIZV_6(2771451) -> phase application received(2771451) -> reception through OLO(2771451) -> send confirmation receipt(2771451) -> send confirmation receipt(2771451) -> forward to the competent authority(2771451) -> regular procedure without MER(2771451) -> send procedure confirmation(2771451) -> extend procedure term(2771451) -> registrer date of publishing received request(2771451) -> WAW permit 

In [ ]:
import openai

client = openai.OpenAI(api_key="")

with open("Trace_text.txt", "r") as f:
    lines = f.readlines()

chunk_size = 20
chunks = [lines[i:i+chunk_size] for i in range(0, len(lines), chunk_size)]

all_results = []

# 각 Chunk에 대해 반복 처리
for i, chunk in enumerate(chunks):
    preprocessed_text = "".join(chunk)


    prompt = f"""
You are a business process analysis expert. The following data represents a process mining event log, where each activity reflects a specific action within a business process. These logs typically include sequences of activities tied to individual case IDs (process instances), and can be used to discover, monitor, and improve real-world processes.

Your task is to detect and correct anomalies in activity labels that contain meaningless or artificially generated suffixes.

Please analyze the following process description and identify any activity names that appear to contain garbled, irrelevant, or randomly generated strings appended to the end of otherwise valid activity names.

Examples (for reference only — not exhaustive):
- Polluted: "register submission date request_RNvnAvOp_560872"
  → Corrected: "register submission date request"
- Polluted: "transcript decision environmental permit to stakeholders_DmQUbIVJ_560462"
  → Corrected: "transcript decision environmental permit to stakeholders"

Detection Criteria:
- The core activity name is a valid business process term.
- The suffix (after an underscore) is meaningless, random, or non-informative.
- Do not include activities with typos, casing errors, or missing characters — only suffix pollution.

Each activity label is followed by a case ID in parentheses. For example:
register submission date request_RNvnAvOp_560872(3027880)

In this case, the case ID is 3027880. Use this ID when reporting.

✅ Output format (clear and consistent):
Case ID: <case_id>
Original Activity: <polluted label>
Corrected Activity: <cleaned activity label>

If no anomaly is found in the chunk, return:
No anomaly found.

Process Description:
{preprocessed_text}
"""

    # GPT-3.5-turbo 호출
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a business process analysis expert."},
            {"role": "user", "content": prompt}
        ],
        temperature=0.2,
        max_tokens=3000
    )

    result = response.choices[0].message.content
    all_results.append(result)

    print(f"\n=== 결과 (Chunk {i+1}) ===\n{result}")


with open("trace_corrected.txt", "w", encoding="utf-8") as f:
    for chunk_result in all_results:
        f.write(chunk_result + "\n\n")

print("\n✅ 모든 Chunk 결과 저장 완료: trace_corrected.txt")



=== 결과 (Chunk 1) ===
Here are the detected anomalies in the activity labels along with their corrections:

Case ID: 2760925  
Original Activity: register submission date request_RNvnAvOp_560872  
Corrected Activity: register submission date request  

Case ID: 2771451  
Original Activity: subcases completeness completed_UEXExIZV_6  
Corrected Activity: subcases completeness completed  

Case ID: 2771451  
Original Activity: applicant is stakeholder_sosXGGLu_6  
Corrected Activity: applicant is stakeholder  

Case ID: 2771451  
Original Activity: request complete_MKILUHtB_6  
Corrected Activity: request complete  

Case ID: 2782209  
Original Activity: applicant is stakeholder_rBmVivpB_560912  
Corrected Activity: applicant is stakeholder  

Case ID: 2782209  
Original Activity: WAW permit aspect_YxgefNvV_560890  
Corrected Activity: WAW permit aspect  

Case ID: 2782209  
Original Activity: grounds for refusal_KIlRmAJm_560890  
Corrected Activity: grounds for refusal  

Case ID: 27822

In [18]:
import pandas as pd
import re

# 1. 정답지 로드
gt = pd.read_csv("/content/오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-01.정답지.csv")

# 2. Injection 값이 'polluted Label(Activity)'인 경우만 오류로 간주
gt["is_polluted"] = gt["Injection"] == "polluted Label(Activity)"
gt["Activity"] = gt["Activity"].astype(str)

# 3. 오류로 라벨링된 Activity만 추출
ground_truth_activities = set(gt[gt["is_polluted"]]["Activity"])

# 4. trace_corrected.txt에서 Original Activity만 추출
predicted_activities = set()
with open("trace_corrected.txt", "r", encoding="utf-8") as f:
    for line in f:
        match = re.search(r"Original Activity\s*:\s*(.+)", line)
        if match:
            activity = match.group(1).strip()
            activity = re.sub(r"\s*\(\d+\)", "", activity)  # 괄호 내 숫자 제거
            predicted_activities.add(activity)

# 5. 정확도 계산
tp = len(predicted_activities & ground_truth_activities)  # 정탐
fp = len(predicted_activities - ground_truth_activities)  # 오탐
fn = len(ground_truth_activities - predicted_activities)  # 미탐

precision = tp / (tp + fp) if (tp + fp) else 0.0
recall = tp / (tp + fn) if (tp + fn) else 0.0
f1 = 2 * precision * recall / (precision + recall) if (precision + recall) else 0.0

# 6. 결과 출력
print(f"True Positives: {tp}")
print(f"False Positives: {fp}")
print(f"False Negatives: {fn}")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1 Score:  {f1:.4f}")


True Positives: 1016
False Positives: 51
False Negatives: 1668
Precision: 0.9522
Recall:    0.3785
F1 Score:  0.5417


In [12]:
import pandas as pd
import re

# 1. trace_corrected.txt에서 수정 매핑 딕셔너리 추출
corrections = {}
with open("trace_corrected.txt", "r", encoding="utf-8") as f:
    lines = f.readlines()

original = None
corrected = None

for line in lines:
    if "Original Activity:" in line:
        original = line.split("Original Activity:")[1].strip()
    elif "Corrected Activity:" in line:
        corrected = line.split("Corrected Activity:")[1].strip()
        if original and corrected:
            corrections[original] = corrected
            original = None
            corrected = None

# 2. 원본 CSV 불러오기
df = pd.read_csv("/content/오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-0.csv")

# 3. Activity 수정 적용
df["Activity"] = df["Activity"].apply(lambda x: corrections.get(x, x))

# 4. 결과 저장
df.to_csv("final_fixed.csv", index=False)
print("✅ 수정된 CSV가 f21inal_fixed.csv 로 저장되었습니다.")


✅ 수정된 CSV가 f21inal_fixed.csv 로 저장되었습니다.


In [13]:
import pandas as pd

# 원본과 수정된 CSV 파일 불러오기
original_df = pd.read_csv("오염 (뒤에 resource 숫자 추가, 랜덤 O)-0.1-0.csv")
fixed_df = pd.read_csv("final_fixed.csv")

# Activity 열 비교
total_rows = len(original_df)
different_rows = (original_df["Activity"] != fixed_df["Activity"]).sum()

# 오차율 계산
error_rate = different_rows / total_rows

# 결과 출력
print(f"총 행 수: {total_rows}")
print(f"Activity가 다른 행 수: {different_rows}")
print(f"오차율 (다른 비율): {error_rate:.4f}")


총 행 수: 26836
Activity가 다른 행 수: 1016
오차율 (다른 비율): 0.0379


In [19]:
import pandas as pd

# 1. 원본 CSV 파일 로드
file_path = "/content/Credit-TRAIN-HOMONYM-0.1-0.csv"  # 엑셀에서 저장한 CSV 파일 경로
df = pd.read_csv(file_path)

# 2. Injection 열 제거
df = df.drop(columns=["Injection"])

# 3. 수정된 데이터프레임을 새 CSV로 저장
df.to_csv("Credit-TRAIN-HOMONYM-0.1-0_no_injection.csv", index=False)

print("✅ Injection 열 제거 완료! 'Credit-TRAIN-HOMONYM-0.1-0_no_injection.csv'로 저장됨.")


✅ Injection 열 제거 완료! 'Credit-TRAIN-HOMONYM-0.1-0_no_injection.csv'로 저장됨.


In [20]:
import pandas as pd

file_path = "/content/Credit-TRAIN-HOMONYM-0.1-0_no_injection.csv"
df = pd.read_csv(file_path)

# Case별로 Activity 리스트 구성
trace_dict = df.groupby("Case")["Activity"].apply(list)

variant_dict = {}

# 각 Case ID에 대해 Activity 시퀀스를 문자열로 변환
for case_id, trace in trace_dict.items():
    # 각 activity 뒤에 (Case ID) 추가
    trace_with_case = [f"{activity}({case_id})" for activity in trace]
    trace_str = " -> ".join(trace_with_case)
    variant_dict[trace_str] = variant_dict.get(trace_str, 0) + 1

# 결과 출력
for i, (variant, count) in enumerate(variant_dict.items(), 1):
    print(f"Variant {i}: {variant} (Count: {count})")

# 파일 저장
with open("Trace_text_credit.txt", "w", encoding="utf-8") as f:
    for i, (variant, count) in enumerate(variant_dict.items(), 1):
        f.write(f"Variant {i}: {variant} (Count: {count})\n")

print("✅ Trace Variants 전처리 완료 및 저장 완료!")


/usr/local/lib/python3.11/dist-packages/cudf/core/groupby/groupby.py:1759: RuntimeWarning: GroupBy.apply() performance scales poorly with number of groups. Got 4000 groups. Some functions may perform better by passing engine='jit'
  warnings.warn(


Variant 1: Check for completeness(0) -> New online application received(0) -> Perform checks(0) -> Make decision(0) -> Notify accept(0) -> Deliver card(0) -> EVENT 13 END(0) (Count: 1)
Variant 2: Check for completeness(1) -> New online application received(1) -> Perform checks(1) -> Make decision(1) -> Notify accept(1) -> Deliver card(1) -> EVENT 13 END(1) (Count: 1)
Variant 3: Check for completeness(2) -> New online application received(2) -> application check(2) -> Make decision(2) -> Notify accept(2) -> Deliver card(2) -> EVENT 13 END(2) (Count: 1)
Variant 4: Check for completeness(3) -> New online application received(3) -> Request info(3) -> info received(3) -> Check for completeness(3) -> Perform checks(3) -> Make decision(3) -> notify reject(3) -> time out(3) -> EVENT 13 END(3) (Count: 1)
Variant 5: Check for completeness(4) -> New online application received(4) -> Request info(4) -> info received(4) -> Check for completeness(4) -> Perform checks(4) -> Make decision(4) -> Notify

In [ ]:
import openai

client = openai.OpenAI(api_key="")

with open("Trace_text_credit.txt", "r") as f:
    lines = f.readlines()

chunk_size = 20
chunks = [lines[i:i+chunk_size] for i in range(0, len(lines), chunk_size)]

all_results = []

# 각 Chunk에 대해 반복 처리
for i, chunk in enumerate(chunks):
    preprocessed_text = "".join(chunk)


    prompt = f"""
You are a business process analysis expert. The following data represents a process mining event log, where each activity reflects a specific action within a business process. These logs typically include sequences of activities tied to individual case IDs (process instances), and can be used to discover, monitor, and improve real-world processes.

Your task is to detect and correct anomalies in activity labels caused by **homonym or semantic confusion** — where an incorrect synonym or semantically similar phrase is used instead of the correct activity label.

Please analyze the following process description and identify any activity names that **should be corrected to the standard term used in the business process**, based on meaning or context.

🧠 Examples of typical homonym errors (for reference only — not exhaustive):
- Polluted: "application check"
  → Corrected: "perform checks"
- Polluted: "receive information"
  → Corrected: "new online application received"
- Polluted: "request information"
  → Corrected: "request info"
- Polluted: "decision making"
  → Corrected: "make decision"

Detection Criteria:
- The activity uses a synonym or reworded phrase that differs from the standard activity label.
- Focus only on semantic or meaning-based differences, not spelling, casing, or formatting.
- Use your knowledge of typical business process terminology to determine the correct label.

Each activity label is followed by a case ID in parentheses. For example:
application check(1234567)

In this case, the case ID is 1234567. Use this ID when reporting.

✅ Output format (clear and consistent):
Case ID: <case_id>
Original Activity: <homonym label>
Corrected Activity: <standardized label>

If no anomaly is found in the chunk, return:
No anomaly found.

Process Description:

{preprocessed_text}
"""

    # GPT-3.5-turbo 호출
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a business process analysis expert."},
            {"role": "user", "content": prompt}
        ],
        temperature=0.2,
        max_tokens=3000
    )

    result = response.choices[0].message.content
    all_results.append(result)

    print(f"\n=== 결과 (Chunk {i+1}) ===\n{result}")


with open("trace_corrected_credit.txt", "w", encoding="utf-8") as f:
    for chunk_result in all_results:
        f.write(chunk_result + "\n\n")

print("\n✅ 모든 Chunk 결과 저장 완료: trace_corrected_credit.txt")


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
Case ID: 1401  
Original Activity: application check  
Corrected Activity: perform checks  

Case ID: 1402  
Original Activity: receive information  
Corrected Activity: new online application received  

Case ID: 1403  
Original Activity: Request info  
Corrected Activity: request information  

Case ID: 1404  
Original Activity: request information  
Corrected Activity: request info  

Case ID: 1406  
Original Activity: request information  
Corrected Activity: request info  

Case ID: 1410  
Original Activity: application check  
Corrected Activity: perform checks  

Case ID: 1412  
Original Activity: notify reject  
Corrected Activity: notify rejection  

Case ID: 1414  
Original Activity: notify reject  
Corrected Activity: notify rejection  

Case ID: 1416  
Original Activity: request information  
Corrected Activity: request info  

Case ID: 1418  
Original Activity: request information  
Corrected Activity: request info  

Case ID: 1421  
Ori

In [26]:
import pandas as pd
import re

# 1. 정답지 로드
gt = pd.read_csv("/content/Credit-TRAIN-HOMONYM-0.1-0.csv")

# 2. Injection 값이 비어 있지 않은 경우를 오류로 간주
gt["is_polluted"] = gt["Injection"].notna()
gt["Activity"] = gt["Activity"].astype(str)

# 3. 오류로 라벨링된 Activity만 추출
ground_truth_activities = set(gt[gt["is_polluted"]]["Activity"])

# 4. trace_corrected.txt에서 Original Activity만 추출
predicted_activities = set()
with open("trace_corrected.txt", "r", encoding="utf-8") as f:
    for line in f:
        match = re.search(r"Original Activity\s*:\s*(.+)", line)
        if match:
            activity = match.group(1).strip()
            activity = re.sub(r"\s*\(\d+\)", "", activity)  # 괄호 내 숫자 제거
            predicted_activities.add(activity)

# 5. 정확도 계산
tp = len(predicted_activities & ground_truth_activities)  # 정탐
fp = len(predicted_activities - ground_truth_activities)  # 오탐
fn = len(ground_truth_activities - predicted_activities)  # 미탐

precision = tp / (tp + fp) if (tp + fp) else 0.0
recall = tp / (tp + fn) if (tp + fn) else 0.0
f1 = 2 * precision * recall / (precision + recall) if (precision + recall) else 0.0

# 6. 결과 출력
print(f"True Positives: {tp}")
print(f"False Positives: {fp}")
print(f"False Negatives: {fn}")
print(f"Precision: {precision:.4f}")
print(f"Recall:    {recall:.4f}")
print(f"F1 Score:  {f1:.4f}")


True Positives: 4
False Positives: 9
False Negatives: 0
Precision: 0.3077
Recall:    1.0000
F1 Score:  0.4706
